# Data Cleaning Techniques in PySpark

In [0]:
from pyspark.sql.functions import col, when, isnan, count, lit, regexp_replace, to_timestamp
from pyspark.sql.types import IntegerType, DoubleType, TimestampType, StringType

## Identifying Data Issues

In [0]:
# Load our messy dataset to demonstrate cleaning techniques
file_path = "/pyspark/video-streaming-data/module3-transform/cleaning/messy_events.csv"
messy_df = spark.read.option("header", "true").option("inferSchema", "true").csv(file_path)

# Look at the schema
print("Schema of our messy data:")
messy_df.printSchema()

Schema of our messy data:
root
 |-- event_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- content_id: string (nullable = true)
 |-- timestamp: timestamp (nullable = true)
 |-- duration_seconds: string (nullable = true)
 |-- device_type: string (nullable = true)
 |-- quality: string (nullable = true)
 |-- buffering_count: integer (nullable = true)
 |-- error_type: string (nullable = true)
 |-- ip_address: string (nullable = true)
 |-- country: string (nullable = true)
 |-- session_id: string (nullable = true)



In [0]:
messy_df.display()

event_id user_id content_id timestamp duration_seconds device_type quality buffering_count error_type ip_address country session_id EVT10000 USR41813 CON10763 2023-09-03T09:18:59Z 565 Web HD 4 null 72.119.240.124 ES SES10000 EVT10001 USR46484 CON12784 2023-09-09T11:44:27Z 2018 Web HD 1 null 156.3.251.123 FR SES10001 EVT10002 null CON16367 2023-09-09T16:51:53Z 2900 TV 4K 3 null 182.53.26.241 AU SES10002 EVT10003 USR46584 CON18916 2023-09-13T08:03:13Z 3242 Tablet 4K 3 null 9.203.70.180 FR SES10003 EVT10004 null CON18924 2023-09-04T13:07:20Z 4248 TV 4K 1 null 152.202.251.124 NL SES10004 EVT10005 USR26888 CON13567 2023-09-13T22:44:28Z 885 TV HD 2 null 12.248.203.140 DE SES10005 EVT10006 USR58686 CON13571 2023-09-13T21:54:05Z 594 Web HD 1 null 118.180.35.136 FR SES10006 EVT10007 USR59173 CON19019 2023-09-14T12:36:36Z 21955 TV 4K 1 null 53.80.37.14 CA SES10007 EVT10008 USR33266 CON15649 2023-09-04T03:11:27Z 9039 TV HD 2 null 123.155.41.53 UK SES10008 EVT10009 USR56453 CON19816 2023-09-03T02:02:33Z 2262 Mobile SD 2 null 67.182.148.182 IT SES10009 EVT10010 USR20454 CON14426 2023-09-06T09:16:48Z 11332 Mobile HD 1 null 95.14.191.161 CA SES10010 EVT10011 USR25422 CON10527 2023-09-02T07:42:35Z 1591 TV 4K 0 network_error 46.247.199.70 ES SES10011 EVT10012 null CON13125 2023-09-10T19:31:59Z 2674 TV 4K 4 null 79.236.29.41 AU SES10012 EVT10013 USR43589 CON19200 2023-09-11T02:31:45Z 2016 Web HD 2 null 118.236.130.132 MX SES10013 EVT10014 USR42089 CON10815 2023-09-02T06:59:54Z 1849 Tablet HD 1 null 212.156.236.142 UK SES10014 EVT10015 USR36996 CON10882 2023-09-02T10:17:24Z 3900 Tablet HD 3 null 140.141.149.122 MX SES10015 null USR26990 CON13135 2023-09-01T07:18:31Z 2622 Tablet HD 2 null 125.115.59.5 FR SES10016 EVT10017 USR47542 CON15474 2023-09-10T11:50:18Z 3771s TV 4K 6 null 218.153.134.228 IT SES10017 EVT10018 USR45730 CON15130 2023-09-08T15:44:37Z 5425 Mobile HD 1 null 156.18.207.226 FR SES10018 EVT10019 USR11535 CON18010 2023-09-05T08:56:23Z 1855 Tablet HD 1 null 174.215.247.65 UK SES10019 null USR56505 CON10749 null 2364 Web HD 2 null 80.85.174.53 ES SES10020 EVT10021 USR52323 CON14582 2023-09-04T14:10:59Z 2672 TV HD 2 server_error 52.165.91.37 IT SES10021 EVT10022 USR11351 CON10167 2023-09-13T23:37:14Z 3639 Mobile HD 1 null 179.87.46.218 BR SES10022 EVT10023 USR20923 CON15519 2023-09-05T14:32:12Z 4347 TV 4K 3 content_unavailable 125.60.41.87 ES SES10023 EVT10024 USR44287 null 2023-09-09T21:51:44Z 975 Web HD 4 null 58.18.29.167 FR SES10024 EVT10025 USR28255 CON11878 2023-09-06T13:34:59Z 2597 Mobile HD 1 null 138.105.85.203 US SES10025 EVT10026 USR29683 CON11133 2023-09-10T04:57:21Z 1068 TV 4K 3 server_error 39.15.228.149 JP SES10026 EVT10027 USR41747 CON14727 2023-09-12T20:00:54Z 2801 Web HD 1 null 150.246.198.57 IT SES10027 EVT10028 USR22166 CON15872 2023-09-06T21:12:18Z 4227 Web HD 4 null 102.136.48.112 BR SES10028 EVT10029 USR51881 CON18829 2023-09-09T16:34:37Z 2590 Web SD 4 null 191.129.16.31 MX SES10029 EVT10030 USR39433 CON12562 2023-09-14T06:28:04Z 4993 Web 4K 2 network_error 48.84.121.164 IT SES10030 EVT10031 USR22623 CON10741 2023-09-08T21:16:00Z 1155 Mobile HD 0 null 211.153.50.236 DE SES10031 EVT10032 USR19867 CON12590 2023-09-04T01:35:28Z 3993 Tablet HD 0 null 158.189.192.148 MX SES10032 EVT10033 USR27444 CON17504 2023-09-05T02:13:58Z 1095 Mobile SD 2 null 125.183.106.186 FR SES10033 null USR48717 CON15520 2023-09-11T13:48:39Z 1375 Tablet 4K 2 network_timeout 83.5.82.9 ES SES10034 EVT10035 USR50836 CON14016 2023-09-14T10:39:57Z 292 Mobile HD 2 null 200.96.185.165 IT SES10035 EVT10036 USR57012 CON19158 2023-09-11T12:52:33Z 1232 Web SD 1 null 38.137.181.145 ES SES10036 EVT10037 USR43857 CON10287 2023-09-08T21:33:48Z 16987 Mobile HD 5 null 141.148.231.255 FR SES10037 EVT10038 USR25738 null 2023-09-10T03:05:28Z 1815 Tablet SD 4 null 42.61.193.245 BR SES10038 null USR56356 CON18675 2023-09-05T09:41:42Z 1569 Tablet 4K 0 null 65.26.141.194 DE SES10039 null USR25902 CON17497 2023-09-09T05:12:14Z 10883 Mobile 4K 1 null 80.161.148.114 U

In [0]:
# How many records do we have?
print("Total number of records:", messy_df.count())

Total number of records: 52500


In [0]:
# Check for nulls
null_counts = messy_df.select([count(when(col(c).isNull(), c)).alias(c) for c in messy_df.columns])
display(null_counts)

event_id user_id content_id timestamp duration_seconds device_type quality buffering_count error_type ip_address country session_id 2608 2637 2629 2607 0 0 0 0 47200 0 0 0

In [0]:
# Check for duplicates
duplicate_count = messy_df.count() - messy_df.dropDuplicates().count()
print(f"Number of duplicate records: {duplicate_count}")


Number of duplicate records: 2500


In [0]:
# Check for type issues
print("Sample of duration_seconds values:")
messy_df.select("duration_seconds").distinct().limit(5).display()

Sample of duration_seconds values:


duration_seconds 11332 2904 1090 691 467

## Cleaning Process

In [0]:
# 1. Remove duplicate rows
clean_df = messy_df.dropDuplicates()
print(f"Records after removing duplicates: {clean_df.count()}")

Records after removing duplicates: 50000


In [0]:
# First, the error_type column - null here means "no error"
clean_df = clean_df.na.fill({"error_type": "none"})

# For key identifier columns - events without IDs aren't useful, so drop these rows
critical_columns = ["user_id", "content_id", "event_id","timestamp"]
clean_df = clean_df.dropna(subset=critical_columns)
print(f"Records after dropping rows with missing IDs: {clean_df.count()}")

Records after dropping rows with missing IDs: 40748


In [0]:
# 3. Fix data type issues for duration_seconds
clean_df = clean_df.withColumn(
    "duration_seconds",
    when(col("duration_seconds").cast("integer").isNull(),
         regexp_replace(col("duration_seconds"), "[^0-9]", "").cast("integer")
    ).otherwise(col("duration_seconds").cast("integer"))
)
clean_df.printSchema()

root
 |-- event_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- content_id: string (nullable = true)
 |-- timestamp: timestamp (nullable = true)
 |-- duration_seconds: integer (nullable = true)
 |-- device_type: string (nullable = true)
 |-- quality: string (nullable = true)
 |-- buffering_count: integer (nullable = true)
 |-- error_type: string (nullable = false)
 |-- ip_address: string (nullable = true)
 |-- country: string (nullable = true)
 |-- session_id: string (nullable = true)



In [0]:
# 5. Verify our cleaned data
print("Null count in critical columns:")
clean_df.select([count(when(col(c).isNull(), c)).alias(c) 
                for c in ["user_id", "content_id", "timestamp"]]).display()

Null count in critical columns:


user_id content_id timestamp 0 0 0

In [0]:
clean_df.display()

event_id user_id content_id timestamp duration_seconds device_type quality buffering_count error_type ip_address country session_id EVT10055 USR58667 CON13530 2023-09-11T09:15:08Z 3337 Tablet HD 2 none 132.115.188.195 IT SES10055 EVT10208 USR53851 CON17461 2023-09-06T23:16:39Z 189 Web HD 2 content_unavailable 32.41.65.15 ES SES10208 EVT10366 USR56472 CON11159 2023-09-01T00:24:29Z 1687 Tablet HD 0 none 58.91.186.209 DE SES10366 EVT10700 USR21119 CON12457 2023-09-08T12:33:15Z 279 TV 4K 4 content_unavailable 199.99.169.130 IT SES10700 EVT10903 USR53432 CON17698 2023-09-01T06:47:13Z 1202 Web HD 4 none 29.146.120.117 IT SES10903 EVT12012 USR26775 CON12162 2023-09-14T06:23:04Z 1205 TV HD 3 none 201.66.91.167 NL SES12012 EVT12369 USR11329 CON17702 2023-09-02T17:49:54Z 2072 Web HD 4 none 212.215.103.104 UK SES12369 EVT12449 USR46104 CON14114 2023-09-09T16:50:35Z 584 Tablet SD 4 none 109.215.149.205 AU SES12449 EVT12890 USR10962 CON13892 2023-09-10T13:15:17Z 4533 Web HD 1 none 12.44.172.92 CA SES12890 EVT12926 USR44825 CON11499 2023-09-08T08:06:50Z 2086 Mobile SD 0 none 35.68.25.19 FR SES12926 EVT12962 USR16582 CON19161 2023-09-08T21:45:27Z 3411 Mobile HD 3 none 141.72.155.170 MX SES12962 EVT13306 USR37542 CON16044 2023-09-10T02:25:53Z 3052 TV 4K 6 none 71.110.170.71 ES SES13306 EVT13410 USR57036 CON11882 2023-09-04T14:52:43Z 748 Tablet HD 3 none 139.28.6.91 ES SES13410 EVT13670 USR31023 CON14043 2023-09-09T16:48:20Z 2773 TV 4K 4 none 4.163.50.177 JP SES13670 EVT13683 USR53790 CON19974 2023-09-03T14:07:05Z 1846 Mobile HD 1 none 26.202.131.233 FR SES13683 EVT13798 USR38724 CON15218 2023-09-02T11:06:26Z 8346 Mobile SD 1 none 32.204.208.90 ES SES13798 EVT13941 USR13272 CON18128 2023-09-13T14:53:01Z 2398 Web HD 2 server_error 6.193.201.197 NL SES13941 EVT14540 USR33047 CON10904 2023-09-13T09:43:00Z 16348 TV 4K 0 none 215.146.65.154 BR SES14540 EVT14927 USR51385 CON11208 2023-09-05T22:31:53Z 8733 Web SD 2 none 212.55.49.6 AU SES14927 EVT15322 USR33270 CON11305 2023-09-09T23:35:54Z 753 Mobile HD 2 none 129.61.157.171 US SES15322 EVT15378 USR39975 CON15969 2023-09-05T10:15:29Z 17152 TV 4K 2 none 118.178.232.97 IT SES15378 EVT15476 USR13471 CON16728 2023-09-09T18:31:31Z 7925 Tablet SD 1 none 173.90.86.202 BR SES15476 EVT15646 USR50621 CON15566 2023-09-05T19:49:46Z 3327 Web 4K 3 server_error 16.35.55.24 ES SES15646 EVT16122 USR20098 CON15926 2023-09-07T22:53:47Z 259 TV 4K 6 none 41.6.14.48 FR SES16122 EVT16459 USR25268 CON11788 2023-09-08T09:50:37Z 4172 TV HD 3 none 82.234.106.105 IT SES16459 EVT16684 USR43719 CON16285 2023-09-03T16:48:03Z 18682 Mobile HD 1 none 193.119.176.111 NL SES16684 EVT16872 USR47918 CON17564 2023-09-01T21:14:17Z 8621 Tablet SD 1 none 61.201.34.211 IT SES16872 EVT17147 USR49621 CON16624 2023-09-12T18:32:39Z 2020 Mobile 4K 3 none 209.224.118.40 FR SES17147 EVT17267 USR44106 CON14172 2023-09-01T07:14:55Z 2790 Mobile 4K 0 none 151.89.155.64 NL SES17267 EVT17506 USR32437 CON11126 2023-09-12T02:31:48Z 6708 TV 4K 1 none 175.68.48.152 ES SES17506 EVT17588 USR27165 CON11386 2023-09-01T22:38:37Z 2908 Web SD 4 none 98.182.233.86 ES SES17588 EVT17638 USR17701 CON10371 2023-09-14T01:06:46Z 756 Tablet HD 3 none 176.6.243.168 NL SES17638 EVT17956 USR18216 CON13856 2023-09-09T05:14:03Z 4329 TV HD 2 none 47.146.173.101 DE SES17956 EVT18108 USR24643 CON10576 2023-09-10T18:29:41Z 17893 TV 4K 2 none 178.86.251.192 DE SES18108 EVT18129 USR51284 CON10351 2023-09-04T03:16:03Z 318 Web 4K 3 none 7.217.124.234 JP SES18129 EVT18556 USR52704 CON11247 2023-09-12T12:51:20Z 517 TV HD 2 none 125.254.95.126 AU SES18556 EVT18783 USR27837 CON15202 2023-09-04T04:08:17Z 7569 Web HD 2 none 93.156.154.184 AU SES18783 EVT19302 USR43783 CON19422 2023-09-03T06:37:45Z 4116 Mobile SD 1 none 184.121.140.145 JP SES19302 EVT19411 USR58431 CON17461 2023-09-02T17:10:40Z 1221 Tablet HD 3 none 200.223.173.48 MX SES19411 EVT19703 USR30535 CON14014 2023-09-06T19:07:35Z 1815 Tablet 4K 2 none 142.53.112.190 UK SES19703 EVT19886 USR12933 CON13451 2023-09-11T07:05:04Z 4838 Mo

In [0]:
# 6. Save the cleaned data
output_path = "pyspark/video-streaming-data/module3-transform/cleaning/our_cleaned_output"
clean_df.write.mode("overwrite").parquet(output_path)

print(f"Cleaned data saved to {output_path}")

Cleaned data saved to pyspark/video-streaming-data/module3-transform/cleaning/our_cleaned_output


In [0]:
# Key Takeaways
print("Data Cleaning Techniques Demonstrated:")
print("1. Removing duplicate rows with dropDuplicates()")
print("2. Handling missing values with fillna() and dropna()")
print("3. Type casting with cast() and when() functions")
print("4. String manipulation with regexp_replace()")
print("5. Filtering invalid data with filter()")

In [0]:
dbutils.fs.rm("dbfs:/pyspark/video-streaming-data/module3-transform/cleaning/our_cleaned_output", recurse=True)